In [1]:
# taken from example gen

import os
import tfx
#from tfx.utils.dsl_utils import external_input - deprecated
from tfx.proto import example_gen_pb2
from tfx.components import CsvExampleGen

# define the path to the data
base_dir = os.getcwd()
data_path = "/home/lunet/ttrmc/mlops/building-machine-learning-pipelines/building-machine-learning-pipelines-examples_based_on_tfx_1.4/data"

data_dir = os.path.join(base_dir, data_path)

# configure the dataset using protobuf
output = example_gen_pb2.Output(
    split_config = example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name='train', hash_buckets=6),
        example_gen_pb2.SplitConfig.Split(name='eval', hash_buckets=2),
        example_gen_pb2.SplitConfig.Split(name='test', hash_buckets=2),
    ]))

# start the tfx pipeline
example_gen = CsvExampleGen(input_base=data_dir,output_config=output)

In [2]:
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
context = InteractiveContext(pipeline_root='./tfx')
context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 1
        type_id: 14
        uri: "./tfx/CsvExampleGen/examples/1"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"test\"]"
          }
        }
        custom_properties {
          key: "file_format"
          value {
            string_value: "tfrecords_gzip"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:single_split,num_files:1,total_bytes:78956236,xor_checksum:1638020131,sum_checksum:1638020131"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            int_value: 0
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        custom_properties {
          key: "tfx_version"
          value {
            string_value: "1.4.0"
          }
        }
        state: LIVE
        , artifact_type: id: 14
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
            additional_properties: {}
            additional_custom_properties: {}
        ))

In [6]:
# rhys follow Chapter 4: Data Validation

import tensorflow_data_validation as tfdv

file_path = data_path + "/consumer_complaints_with_narrative.csv"
stats = tfdv.generate_statistics_from_csv(data_location=file_path,delimiter=',')

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


In [7]:
print(stats)

datasets {
  num_examples: 66799
  features {
    type: STRING
    string_stats {
      common_stats {
        num_non_missing: 66799
        min_num_values: 1
        max_num_values: 1
        avg_num_values: 1.0
        num_values_histogram {
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low

In [8]:
schema = tfdv.infer_schema(stats)

In [9]:
tfdv.display_schema(schema)

Type  Presence Valency              Domain
Feature name                                                                
'product'                       STRING  required                   'product'
'sub_product'                   STRING  optional  single       'sub_product'
'issue'                         STRING  required                     'issue'
'sub_issue'                     STRING  optional  single         'sub_issue'
'consumer_complaint_narrative'   BYTES  required                           -
'company'                        BYTES  required                           -
'state'                         STRING  optional  single             'state'
'zip_code'                       BYTES  optional  single                   -
'company_response'              STRING  required          'company_response'
'timely_response'               STRING  required           'timely_response'
'consumer_disputed'                INT  required                           -

Values
Domain                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
'product'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [11]:
# compare statistics of different datasets
train_data_loc = "/home/lunet/ttrmc/mlops/building-machine-learning-pipelines/building-machine-learning-pipelines-examples_based_on_tfx_1.4/chapters/data_validation/tfx/CsvExampleGen/examples/1/Split-train/data_tfrecord-00000-of-00001.gz"
eval_data_loc = "/home/lunet/ttrmc/mlops/building-machine-learning-pipelines/building-machine-learning-pipelines-examples_based_on_tfx_1.4/chapters/data_validation/tfx/CsvExampleGen/examples/1/Split-eval/data_tfrecord-00000-of-00001.gz"

train_stats = tfdv.generate_statistics_from_tfrecord(data_location=train_data_loc)
eval_stats = tfdv.generate_statistics_from_tfrecord(data_location=eval_data_loc)

tfdv.visualize_statistics(lhs_statistics=eval_stats,rhs_statistics=train_stats,lhs_name='EVAL_DATASET',rhs_name='TRAIN_DATASET')

In [13]:
# anomaly detection

anomalies = tfdv.validate_statistics(statistics=eval_stats,schema=schema)

tfdv.display_anomalies(anomalies)

Anomaly short description  \
Feature name                              
'sub_issue'              Missing values   
'state'                  Missing values   
'sub_product'            Missing values   
'zip_code'               Missing values   

                                     Anomaly long description  
Feature name                                                   
'sub_issue'    Some examples have fewer values than expected.  
'state'        Some examples have fewer values than expected.  
'sub_product'  Some examples have fewer values than expected.  
'zip_code'     Some examples have fewer values than expected.

In [14]:
sub_issue_feature = tfdv.get_feature(schema,'sub_issue')
sub_issue_feature.presence.min_fraction = 0.9

In [16]:
state_domain = tfdv.get_domain(schema,'state')
state_domain.value.remove('AK')

In [19]:
schema_location = base_dir + "/schema"
tfdv.write_schema_text(schema,schema_location)

In [22]:
updated_schema = tfdv.load_schema_text(schema_location) # load a schema proto file
updated_anomalies = tfdv.validate_statistics(eval_stats,updated_schema)
tfdv.display_anomalies(updated_anomalies)

Anomaly short description  \
Feature name                              
'zip_code'               Missing values   
'sub_issue'              Missing values   
'sub_product'            Missing values   
'state'                 Multiple errors   

                                                                                                 Anomaly long description  
Feature name                                                                                                               
'zip_code'                                                                 Some examples have fewer values than expected.  
'sub_issue'                                                                Some examples have fewer values than expected.  
'sub_product'                                                              Some examples have fewer values than expected.  
'state'        Some examples have fewer values than expected. Examples contain values missing from the schema: AK (<1%).

In [23]:
updated_schema

feature {
  name: "product"
  type: BYTES
  domain: "product"
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "sub_product"
  value_count {
    min: 1
    max: 1
  }
  type: BYTES
  domain: "sub_product"
  presence {
    min_count: 1
  }
}
feature {
  name: "issue"
  type: BYTES
  domain: "issue"
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "sub_issue"
  value_count {
    min: 1
    max: 1
  }
  type: BYTES
  domain: "sub_issue"
  presence {
    min_fraction: 0.9
    min_count: 1
  }
}
feature {
  name: "consumer_complaint_narrative"
  type: BYTES
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "company"
  type: BYTES
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "state"
  value_count {
    min: 1


In [27]:
# data skew

tfdv.get_feature(schema,'company').skew_comparator.infinity_norm.threshold = 0.01
skew_anomalies = tfdv.validate_statistics(statistics=train_stats,schema=schema,serving_statistics=eval_stats)
tfdv.display_anomalies(skew_anomalies)

# wrong datasets for this to work - should be returning L-infinity norm information - see book

Anomaly short description  \
Feature name                              
'sub_issue'              Missing values   
'sub_product'            Missing values   
'state'                 Multiple errors   
'zip_code'               Missing values   

                                                                                                 Anomaly long description  
Feature name                                                                                                               
'sub_issue'                                                                Some examples have fewer values than expected.  
'sub_product'                                                              Some examples have fewer values than expected.  
'state'        Some examples have fewer values than expected. Examples contain values missing from the schema: AK (<1%).   
'zip_code'                                                                 Some examples have fewer values than expected.

baseline {
  feature {
    name: "product"
    type: BYTES
    domain: "product"
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "sub_product"
    value_count {
      min: 1
      max: 1
    }
    type: BYTES
    domain: "sub_product"
    presence {
      min_count: 1
    }
  }
  feature {
    name: "issue"
    type: BYTES
    domain: "issue"
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "sub_issue"
    value_count {
      min: 1
      max: 1
    }
    type: BYTES
    domain: "sub_issue"
    presence {
      min_fraction: 0.9
      min_count: 1
    }
  }
  feature {
    name: "consumer_complaint_narrative"
    type: BYTES
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "company"
    type: BYTES
    pr

In [37]:
tfdv.visualize_statistics(lhs_statistics=train_stats)

In [40]:
# slicing

from tensorflow_data_validation.utils import slicing_util

slice_fn1 = slicing_util.get_feature_value_slicer(features={'state': [b'CA']})
slice_options = tfdv.StatsOptions(slice_functions=[slice_fn1])
slice_stats = tfdv.generate_statistics_from_csv(data_location=file_path,delimiter=',',stats_options=slice_options)

In [45]:
## these functions are wrong but we get the principle

from tensorflow_metadata.proto.v0 import statistics_pb2

def display_slice_keys(stats):
    print(list(map(lambda x: x.name, slice_stats.datasets)))
    
def get_sliced_stats(stats,slice_key):
    for stats.name in slice_key:
        if stats.name == slice_key:
            result = statistics_pb2.DatasetFeatureStatisticsList()
            result.datasets.add().CopyFrom(sliced_stats)
            return result
        print('Invalid Slice key')
        
def compare_slices(stats,slice_key1,slice_key2):
    lhs_stats = get_sliced_stats(stats,slice_key1)
    rhs_stats = get_sliced_stats(stats,slice_key2)
    tfdv.visualize_statistics(lhs_stats,rhs_stats)

In [51]:
print(slice_stats.names)

AttributeError: names

In [47]:
tfdv.visualize_statistics(get_sliced_stats(slice_stats,'state_CA'))

AttributeError: 'DatasetFeatureStatisticsList' object has no attribute 'name'